In [17]:
#
# This notebook is for solving the first task from ML course
# Most of this code was taken from https://github.com/andriygav/MachineLearningSeminars/tree/master
# and modified for the purposes of the task
#
# It was run on python 3.10 with libs from requirements.txt 
# although I may have forgotten some of them for visualisation
#

import matplotlib.pyplot as plt
from matplotlib import gritestpec
import seaborn as sns
import pandas as pd

from scipy.special import expit
import numpy as np
import torch

# For interactive plots - makes my pc lag so I did not use it
# !pip install ipympl
# %matplotlib widget

import plotly.express as px
from sklearn.metrics import root_mean_squared_error


In [358]:
ds = pd.read_csv('train.csv')
print(all(ds[['x7', 'x13', 'x14']] == 0.0))
ds

True


index        y    x1  x2  x3  x4  x5      x6   x7      x8      x9  \
0          0   495.67  17.0   1  22   0   1    0.00  0.0  185.18  287.05   
1          1   595.67  21.0   1  32   0   1    0.00  0.0   76.28  522.28   
2          2   786.37  10.0   1  45   1   2    0.00  0.0  131.27  566.15   
3          3  1142.63  10.0   1  41   0   2    0.00  0.0  307.49  926.55   
4          4   567.47  19.0   1  36   0   1    0.00  0.0    4.18  529.77   
...      ...      ...   ...  ..  ..  ..  ..     ...  ...     ...     ...   
15995  15995   459.46  12.0   1  35   0   1  322.38  0.0    5.26  339.56   
15996  15996   203.46  11.0   1  34   0   1    0.00  0.0    2.03  218.02   
15997  15997   220.25  13.0   1  26   0   2   71.39  0.0    0.30   46.04   
15998  15998   447.57  13.0   1  29   0   1  484.69  0.0    1.05  377.44   
15999  15999   110.72  14.0   1  26   0   1   69.45  0.0   20.95   49.21   

        x10    x11     x12  x13  x14   x15    x16  x17      x18  
0      0.85   6.33   54.38  0.0  0.0  0.00  30.54  0.0   509.94  
1      0.00   7.96  190.97  0.0  0.0  0.00   0.00  0.0   606.52  
2      0.00  20.23  328.13  0.0  0.0  8.85   0.00  0.0   726.50  
3      0.00   8.08  351.38  0.0  0.0  0.00   5.05  0.0  1247.17  
4      0.00   0.00    0.00  0.0  0.0  0.00   0.00  0.0   533.95  
...     ...    ...     ...  ...  ...   ...    ...  ...      ...  
15995  0.00   0.00  305.75  0.0  0.0  0.00   0.00  0.0   344.83  
15996  0.04   0.00  163.67  0.0  0.0  0.00   0.00  0.0   220.10  
15997  0.00   0.00   46.34  0.0  0.0  0.00   0.00  0.0    46.34  
15998  0.00   0.00  153.85  0.0  0.0  0.00   0.00  0.0   378.49  
15999  0.00   0.00   33.92  0.0  0.0  1.46   0.00  0.0    71.62  

[16000 rows x 20 columns]

In [359]:
ds.drop(['x7', 'x13', 'x14'], axis=1, inplace=True)
ds.sort_values(by='y', inplace=True)
ds['x0'] = 1 # so no need to add sth later
ds

index        y    x1  x2  x3  x4  x5       x6      x8       x9   x10  \
12630  12630     6.25  13.0   1  32   0   1     3.90    0.00     3.90  0.00   
14840  14840    10.86  11.0   1  24   1   2    54.29    0.65     8.94  0.00   
11567  11567    15.79  11.0   1  22   0   2    40.48    0.09    16.49  0.00   
12164  12164    20.28  10.0   0  22   0   1     0.00    0.60    20.34  0.00   
14957  14957    21.14  15.0   0  40   0   1    14.59    3.31    11.63  0.00   
...      ...      ...   ...  ..  ..  ..  ..      ...     ...      ...   ...   
6371    6371  2688.08  15.0   1  34   0   1  2736.87  362.13  2395.13  0.00   
10970  10970  2688.93  10.0   1  39   0   1  1133.70  887.26   279.15  0.00   
916      916  2691.03  10.0   1  44   0   1     0.00    9.21  2165.67  0.00   
3920    3920  2691.05  10.0   1  27   1   1     0.00  149.96  2020.47  0.00   
2521    2521  2714.44  14.0   1  24   0   1   960.94  253.25   624.78  0.28   

          x11      x12   x15    x16   x17      x18  x0  
12630    0.00     3.90  0.00   0.00  0.00     3.90   1  
14840    0.00     9.58  0.00   0.00  0.00     9.58   1  
11567    0.00     1.42  0.00   0.00  0.00    16.57   1  
12164    0.00    12.59  0.00   0.00  0.00    20.94   1  
14957    0.00     4.81  0.00   0.00  0.00    14.95   1  
...       ...      ...   ...    ...   ...      ...  ..  
6371   174.05  2615.74  1.40   6.51  0.00  2939.22   1  
10970    0.00  1166.41  0.00   0.00  0.00  1166.41   1  
916      0.00    19.27  0.00   0.00  0.00  2174.88   1  
3920     3.51   171.85  0.00   0.76  0.00  2174.70   1  
2521     2.52   777.30  1.64  54.20  0.84   938.36   1  

[16000 rows x 18 columns]

In [371]:
y = ds['y'].values
x = ds.loc[:, (ds.columns != 'y') & (ds.columns != 'index') 
           & (ds.columns != 'x7') & (ds.columns != 'x13') & (ds.columns != 'x14')].values
x, y
xq = ds[['x8','x9','x12','x18']].values

In [22]:
for i in ds.columns:
    if i in {'index', 'y'}:
        continue
    print(i, 100*np.corrcoef(ds[i].values, ds['y'].values)[0,1])

x1 -2.422355677004155
x2 19.55600106335135
x3 10.671738163026115
x4 15.118603956659134
x5 4.712800002647019
x6 30.730133437254786
x7 nan
x8 53.0847772735768
x9 81.4849865035852
x10 3.929429079477286
x11 28.409965906099178
x12 58.3201174408309
x13 nan
x14 nan
x15 14.932865985141323
x16 16.686762984853395
x17 9.84123219501548
x18 85.58578818417752
x0 nan


/home/user/.local/lib/python3.10/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/user/.local/lib/python3.10/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]


In [90]:
def MAPE(y_true, y_pred): 
    y_true, y_pred = np.asarray(y_true), np.asarray(y_pred)
    return (y_true - y_pred) / y_true

def MAPEV(y_true, y_pred):
    return np.mean(np.abs(MAPE(y_true, y_pred)))

# Bad solution

In [83]:
V, d, U = np.linalg.svd(x, full_matrices=False)
D = np.eye(len(d))*d
lambd = d**2
lambd

array([7.92778215e+09, 1.81955948e+09, 2.45048700e+08, 1.21989879e+08,
       2.07324695e+07, 9.80239292e+06, 1.88323113e+06, 1.00840392e+06,
       4.31517268e+05, 1.41265882e+05, 6.02755302e+03, 3.13768299e+03,
       2.93571641e+03, 2.32013427e+03, 3.85543280e+02, 5.02656911e-02])

In [84]:
y

array([   6.25,   10.86,   15.79, ..., 2691.03, 2691.05, 2714.44])

In [86]:
tau = 0

for tau in [0, 1e-5, 1e-4, 1e-3, 0.01, 0.1, 1, 10, 1e5, 1e9]:
    W = (U.T@D@np.linalg.inv(D**2 + tau*np.eye(len(D)))@V.T)@y
    print({
        'y': x@W,
        't': f'{tau=} mape={MAPEV(y, x@W)}',
        #'x': range(len(y_ts))
    })


{'y': array([ 112.80080019,  144.33445343,  118.15425958, ..., 2506.57619382,
       2517.30104329, 1125.49265885]), 't': 'tau=0 mape=0.35196535100024634'}
{'y': array([ 112.80080279,  144.33477901,  118.15458739, ..., 2506.5762241 ,
       2517.30107038, 1125.49232895]), 't': 'tau=1e-05 mape=0.351965356537149'}
{'y': array([ 112.80082617,  144.33770335,  118.15753184, ..., 2506.57649615,
       2517.30131375, 1125.48936574]), 't': 'tau=0.0001 mape=0.35196540626762246'}
{'y': array([ 112.80105534,  144.36638166,  118.1864075 , ..., 2506.57916428,
       2517.30370018, 1125.46030585]), 't': 'tau=0.001 mape=0.3519658938161381'}
{'y': array([ 112.80295555,  144.606019  ,  118.42770939, ..., 2506.60148328,
       2517.32362648, 1125.21743843]), 't': 'tau=0.01 mape=0.35197017219438886'}
{'y': array([ 112.80883761,  145.42217492,  119.25015423, ..., 2506.67845822,
       2517.3908949 , 1124.38861865]), 't': 'tau=0.1 mape=0.3519870439755021'}
{'y': array([ 112.80362742,  145.87037322,  119.71

Above is too bad:(

# Good solution

In [431]:
import scipy.optimize

def calc_y(x_, xq_, w):
    return x_.dot(w[:x_.shape[1]]) + (xq_*xq_).dot(w[x_.shape[1]:])

def train_model(x_, y_, xq_):
    zeros = np.zeros(x.shape[1] + xq_.shape[1])
    return scipy.optimize.fmin_powell(
        lambda w: MAPEV(y_, calc_y(x_, xq_, w)),
        zeros, xtol=1e-6, ftol=1e-12, maxfun=1000000000000
    )    ### gives 0.24229013378518288
    zeros = np.zeros(x.shape[1])
    return scipy.optimize.fmin_powell(
        lambda w: MAPEV(y_, x_.dot(w)),
        zeros, xtol=1e-9, ftol=1e-12, maxfun=1000000000000
    )    ### gives 0.24237535307811858


In [432]:
def finalize(y, y_pred):
    print(MAPEV(y, y_pred))
    return px.line(x=y, y=MAPE(y, y_pred))

In [433]:
allc = train_model(x,y,xq)
# y_pred = x.dot(allc)
y_pred = calc_y(x, xq, allc) # x.dot(allc)
finalize(y, y_pred)

Optimization terminated successfully.
         Current function value: 0.242290
         Iterations: 82
         Function evaluations: 47029
0.24229013378518288


In [345]:
test = pd.read_csv('test.csv')
print(all(test[['x7', 'x13', 'x14']] == 0.0))
test.drop(['x7', 'x13', 'x14'], axis=1, inplace=True)
test['x0'] = 1 # so no need to add sth later
test

True


index    x1  x2  x3  x4  x5       x6      x8      x9  x10    x11     x12  \
0        0  14.0   1  30   1   1     0.00  209.29  358.34  0.0   1.49   33.67   
1        1  14.0   0  26   0   1   154.91   19.08  146.38  0.0   0.00   96.97   
2        2  10.0   1  32   0   1     0.00  121.21  428.18  0.0  17.90   62.89   
3        3  15.0   1  42   1   1  1244.46  407.67  804.93  0.0   9.98  932.81   
4        4  19.0   1  33   0   2  1284.48  196.50  874.94  0.0   9.17  828.86   
..     ...   ...  ..  ..  ..  ..      ...     ...     ...  ...    ...     ...   
995    995  22.0   0  23   0   2     0.00   20.73  130.43  0.0   0.00   45.49   
996    996  23.0   1  45   0   1   233.22   33.31  200.45  0.0   0.24  234.25   
997    997  23.0   1  28   0   1   264.56   14.02  236.66  0.0   0.66  234.80   
998    998  11.0   0  36   0   1     0.00   58.20  217.31  0.0   0.00  139.09   
999    999  11.0   1  58   1   1     0.00   44.52  138.62  0.0   0.36   48.26   

       x15   x16   x17      x18  x0  
0     0.00  1.60  0.00   570.72   1  
1     0.00  0.00  0.00   165.45   1  
2    18.12  0.00  0.00   585.42   1  
3    20.65  2.73  2.28  1250.52   1  
4     0.00  0.21  0.37  1081.56   1  
..     ...   ...   ...      ...  ..  
995   0.00  0.00  0.00   151.16   1  
996   0.25  0.00  0.00   234.25   1  
997   0.00  0.00  0.00   251.34   1  
998   0.00  0.00  0.00   275.50   1  
999   0.90  0.00  0.00   184.41   1  

[1000 rows x 17 columns]

In [361]:
xc = x[y>80]
yc = y[y>80]
normc = train_model(xc,yc)
yc_pred = xc.dot(normc)
finalize(yc, yc_pred)

Optimization terminated successfully.
         Current function value: 0.235859
         Iterations: 26
         Function evaluations: 14167
0.23585941286495768


In [423]:
xt = test.loc[:, (test.columns != 'y') & (test.columns != 'index') 
           & (test.columns != 'x7') & (test.columns != 'x13') & (test.columns != 'x14')].values
xtq = test[['x8','x9','x12','x18']].values
xt

array([[ 14.  ,   1.  ,  30.  , ...,   0.  , 570.72,   1.  ],
       [ 14.  ,   0.  ,  26.  , ...,   0.  , 165.45,   1.  ],
       [ 10.  ,   1.  ,  32.  , ...,   0.  , 585.42,   1.  ],
       ...,
       [ 23.  ,   1.  ,  28.  , ...,   0.  , 251.34,   1.  ],
       [ 11.  ,   0.  ,  36.  , ...,   0.  , 275.5 ,   1.  ],
       [ 11.  ,   1.  ,  58.  , ...,   0.  , 184.41,   1.  ]])

In [424]:
#ypr = xt.dot(normc)
#pd.DataFrame({'index':test['index'], 'y':ypr}).to_csv('result_norm.csv', index=False)
#ypr = xt.dot(allc)
#pd.DataFrame({'index':test['index'], 'y':ypr}).to_csv('result.csv', index=False)
ypq = calc_y(xt, xtq, allc)
pd.DataFrame({'index':test['index'], 'y':ypq}).to_csv('result_quad.csv', index=False)

In [365]:
np.min(y_pred)
np.min(ypr)

92.99707144399008

In [368]:
sorted([i for i in zip(allc, test.columns[(test.columns != 'y') & (test.columns != 'index') 
           & (test.columns != 'x7') & (test.columns != 'x13') & (test.columns != 'x14')])])

[(-0.2003872430646573, 'x1'),
 (-0.027774273491405016, 'x12'),
 (-0.0013445756814017423, 'x6'),
 (0.16392277759805685, 'x3'),
 (0.25984500193348953, 'x18'),
 (0.6002116657020765, 'x15'),
 (0.7387954938636299, 'x9'),
 (0.7505956077578124, 'x8'),
 (0.8392497418676098, 'x11'),
 (1.2372564678058569, 'x16'),
 (1.6321970916213075, 'x17'),
 (3.1500211215399867, 'x5'),
 (4.906835123243735, 'x10'),
 (5.254651776186847, 'x4'),
 (16.11546034951742, 'x2'),
 (19.133695355247283, 'x0')]

# DOWN IS USELESS

Bid drop at y<30

In [95]:
len(y[y<30])/len(y)*100

0.08125

In [105]:
len(y[y<30]), x.shape, y.shape, y[y<30].shape, x[y<30].shape

(13, (16000, 16), (16000,), (13,), (13, 16))

In [129]:
xs, ys = x[y<30], y[y<30]
small = train_model(xs, ys)
xm, ym = x[(y>=30) & (y<100)], y[(y>=30) & (y<100)]
med = train_model(xm, ym)
xmb, ymb = x[(y>=100) & (y<200)], y[(y>=100) & (y<200)]
medbig = train_model(xmb, ymb)
xbs, ybs = x[(y>=200) & (y<750)], y[(y>=200) & (y<750)]
bigsm = train_model(xbs, ybs)
xb, yb = x[y>=750], y[y>=750]
big = train_model(xb, yb)

In [133]:
bigpr = x.dot(big)
bsp = x.dot(bigsm) * (bigpr<750) + bigpr * (bigpr >= 750)
finalize(y, bsp)

0.63502087784483


In [130]:
ysp = xs.dot(small)
ymp = xm.dot(med)
ymbp = xmb.dot(medbig)
ybsp = xbs.dot(bigsm)
ybp = xb.dot(big)
finalize(y, np.concatenate([ysp, ymp, ymbp, ybsp, ybp]))

0.17861325791968058


In [135]:
x.dot(bigsm)

array([ 157.62683859,  176.85962451,  169.79960679, ..., 1649.71640922,
       1660.82064519,  799.48422853])

In [151]:
ds['yc'] = ds['y']
ds['pr'] = x.dot(allc)

In [154]:
np.sort(allc)

array([-2.95155818e-01, -1.36645097e-01, -1.28656200e-01, -1.19681769e-01,
       -5.63164448e-02, -3.05994237e-02, -4.77625616e-03,  3.54417551e-02,
        3.21285068e-01,  4.50125959e-01,  1.14181276e+00,  1.54068136e+00,
        2.77420224e+00,  4.62252085e+00,  8.51253212e+00,  1.54947562e+01])

In [272]:
y0 = x.dot(allc)
MAPEV(y,y0)
#finalize(y, y0)

0.24267871604641822

In [320]:
bst = ((-np.inf, 220), (60, 350), (100, 600), (60, 1500), (600, 2500), (1500, np.inf))
bsr = ((-np.inf, 65), (65, 150), (150, 300), (300, 750), (750, 1750), (1750, np.inf))
ys = [y[(y>=i[0]) & (y<i[1])] for i in bst]
xs = [x[(y>=i[0]) & (y<i[1])] for i in bst]
ms = [train_model(x, y) for x,y in zip(xs, ys)]

In [321]:
gin = [(y0 >= i[0]) & (y0 < i[1]) for i in bsr]
print([sum(i) for i in gin])
print([MAPEV(y[i], x[i].dot(m)) for i, m in zip(gin, ms)])
print([(min(y[i]), max(y[i])) for i, m in zip(gin, ms)])
# y1 = y0 * (gin[1]) + x.dot(ms[0])*gin[0] + x.dot(ms[2])*gin[2]
y1 = sum(x.dot(m)*i for i, m in zip(gin, ms))
print('simple:', 0.24268)
MAPEV(y, y1)
#finalize(y, y1)

[237, 3021, 4957, 6291, 1379, 115]
[0.4195529774210382, 0.32770492881534935, 0.26895698141745167, 0.19618541108647589, 0.1865436838198098, 0.12985884855996827]
[(6.25, 196.89), (36.04, 547.82), (96.1, 1100.12), (235.42, 2647.17), (644.52, 2714.44), (1582.06, 2691.05)]
simple: 0.24268


0.2455643957001999

In [319]:
import plotly.figure_factory as ff
ff.create_distplot([y[gin[2]]], 'y')
#sns.kdeplot(np.array(y[gin[2]]))

In [196]:
[i.shape for i in xs], [i.shape for i in ys]

([(972, 16), (15111, 16), (2274, 16)], [(972,), (15111,), (2274,)])

In [436]:
#finalize(y, x.dot(bigsm))
px.scatter(x=y, y=y_pred)
#px.scatter(ds, x='x18', y=['y'])#['x18', 'x9', 'yc', 'x8', 'x12', 'x6', 'pr'])

In [132]:
test = pd.read_csv('test.csv')
print(all(test[['x7', 'x13', 'x14']] == 0.0))
test.drop(['x7', 'x13', 'x14'], axis=1, inplace=True)
test.sort_values(by='y', inplace=True)
test['x0'] = 1 # so no need to add sth later
test

True


KeyError: 'y'

In [ ]:
y = ds['y'].values
x = ds.loc[:, (ds.columns != 'y') & (ds.columns != 'index') 
           & (ds.columns != 'x7') & (ds.columns != 'x13') & (test.columns != 'x14')].values
x, y